In [1]:
from math import log 
import numpy as np
from loadMnist import load_images, load_labels

In [2]:
# 讀資料
train_data  = load_images("data/train-images.idx3-ubyte")
train_label = load_labels("data/train-labels.idx1-ubyte")
test_data   = load_images("data/t10k-images.idx3-ubyte")
test_label  = load_labels("data/t10k-labels.idx1-ubyte")

In [3]:
# 目標: 紀錄各label機率(P(0),P(1),....)
# 1.創一個字典，紀錄各label數量
label_number_dict = {}
for label in train_label:
    if label in label_number_dict:
        label_number_dict[label] += 1
    else:
        label_number_dict[label] = 1
print("label_number_dict: ", label_number_dict)


# 2. 創一個字典，紀錄各label機率(P(0),P(1),....)
label_probability_dict = {}
for label in label_number_dict:
    label_probability_dict[label] = label_number_dict[label] / 60000
print("label_probability_dict: ", label_probability_dict)

label_number_dict:  {5: 5421, 0: 5923, 4: 5842, 1: 6742, 9: 5949, 2: 5958, 3: 6131, 6: 5918, 7: 6265, 8: 5851}
label_probability_dict:  {5: 0.09035, 0: 0.09871666666666666, 4: 0.09736666666666667, 1: 0.11236666666666667, 9: 0.09915, 2: 0.0993, 3: 0.10218333333333333, 6: 0.09863333333333334, 7: 0.10441666666666667, 8: 0.09751666666666667}


In [4]:
def gussian(pixel_range, mean, var):
    p = 1 / (np.sqrt(2 * np.pi * var)) * np.exp(-(pixel_range - mean) ** 2 / (2 * var))
    return p

# 錯誤: var = 0.00000001??

In [5]:
# 目標: 使用高斯機率，算各別pixel條件機率，例:P(第一格,暗淡=25|label=0)=0.05,P(第一格,暗淡=85|label=0)=0.05,...,P(第七八四格, 暗淡=255|lebel=9)=0.01
# 1.創一個三維 數量 矩陣儲存結果[10*784*256]，先計算train data每一個pixel的mean&var
condiction_probability3D = np.zeros((10,784,256))
for label in range(10):
    temp = train_data[train_label==label]  # 挑出各別label資料算各pixel mean&var
    mean = np.mean(temp, axis=0)
    var  = np.var(temp, axis=0)
    var[var==0] = 100000                # 將var設大，這樣就讓"該pixel" "該灰階色調" 條件機率變小，降低影響
    for i in range(784):
        for pixel_range in range(256):
            condiction_probability3D[label][i][pixel_range] = gussian(pixel_range, mean[i], var[i])   # 高斯機率算每個pixel機率


In [6]:
# 進行test資料集，連續版本運算
error = 0
for j in range(len(test_data)): 
    prob_sum = 0
    prob_logs = []
    for label in range(10):
        prob_log = 0
        for i, pixel in enumerate(test_data[j]):  
            pixel_range = pixel
            prob_log += log(max(1e-125, condiction_probability3D[label][i][pixel_range]))  # log x越接近0,y越接近負無限大,又因為log0不存在，所以將機率0設定一個非常接近零的數值當屏障 

        prob_logs.append(prob_log + log(label_probability_dict[label]))  # 最後要乘P(label)的機率
        prob_sum += prob_log + log(label_probability_dict[label])
    
    # 印出結果 #
    print("Postirior (in log scale):")
    log_result = np.array(prob_logs)/prob_sum
    for i, v in enumerate(log_result):
        print("{}: {}".format(i, v))
    pred = np.argmin(log_result)         # 因為開log，所以要選最小的才是機率最高的
    ans  = test_label[j] 
    print("Prediction: {}, Ans: {}".format(pred, ans))
    print()
    if pred != ans:
        error += 1
    
# 計算錯誤率 #
error_rate = error/len(test_data)
print("Error rate: {}".format(error_rate))

Postirior (in log scale):
0: 0.0994124884407488
1: 0.15362375751313037
2: 0.10177760165315283
3: 0.09528610011925558
4: 0.09127043514593551
5: 0.09027981660736942
6: 0.11722561064825682
7: 0.07424035359718673
8: 0.09769729808277677
9: 0.07918653819218718
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.08538474041613654
1: 0.13955971254781604
2: 0.05540747120163542
3: 0.08158440700823064
4: 0.10348284253988367
5: 0.08664340008046774
6: 0.08452461773127541
7: 0.14318827632551948
8: 0.09739946660897573
9: 0.12282506554005942
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.10722192888768359
1: 0.07970513660630663
2: 0.09687833921237061
3: 0.09805883794532405
4: 0.09771677795579858
5: 0.09869798480139953
6: 0.10027173362142464
7: 0.11248230290390247
8: 0.09984444587808115
9: 0.10912251218770894
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.07350785235010267
1: 0.2617022086647302
2: 0.07685209061277794
3: 0.07784579523908176
4: 0.07986966150459492
5: 0.0774619944135579
6:

5: 0.0977488844809625
6: 0.09850214046101952
7: 0.1122841173086675
8: 0.09930078785426215
9: 0.11239023986790099
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10362902914426993
1: 0.16481249099577
2: 0.10680527898145671
3: 0.08396830217284458
4: 0.08814613333307265
5: 0.08624105359112405
6: 0.10487807189508663
7: 0.08544441396357351
8: 0.08798352743136993
9: 0.08809169849143197
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.10797128108194651
1: 0.08308477117486815
2: 0.10014423628068023
3: 0.09861913472824171
4: 0.0985510769307429
5: 0.0995650455792147
6: 0.11227775664739896
7: 0.09870405456298223
8: 0.10125705399951296
9: 0.09982558901441171
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.09076732313141775
1: 0.16926946612398802
2: 0.08753156999659849
3: 0.08074423654599652
4: 0.08462127277598534
5: 0.08337564056764878
6: 0.11892014518047453
7: 0.09636506188646107
8: 0.08534916521728561
9: 0.10305611857414403
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.0

Postirior (in log scale):
0: 0.09188427485378123
1: 0.21989238401770783
2: 0.07468583324310127
3: 0.0879079066850316
4: 0.09531462621784552
5: 0.082635488136494
6: 0.07790758653459517
7: 0.09289447262888426
8: 0.08701557354431624
9: 0.08986185413824294
Prediction: 2, Ans: 6

Postirior (in log scale):
0: 0.08167649564982025
1: 0.21601340717099407
2: 0.08264869453901807
3: 0.09120350691552215
4: 0.07338467664771972
5: 0.08068848511500061
6: 0.09507945467970302
7: 0.09420689454920701
8: 0.09465835015128736
9: 0.09044003458172768
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.09884547865712907
1: 0.14294694965466778
2: 0.0908067238715924
3: 0.08474488172900321
4: 0.08875924450555972
5: 0.0877507940933286
6: 0.12473127190236358
7: 0.09669765616644602
8: 0.08818965231759415
9: 0.09652734710231546
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.05686261772516521
1: 0.2671355659556235
2: 0.07313416013738067
3: 0.10703580421349933
4: 0.07104697665607705
5: 0.07702049126247852
6: 0.

Postirior (in log scale):
0: 0.06839143282866568
1: 0.2244362141044869
2: 0.06445243785495232
3: 0.06756959547531363
4: 0.09280216845804906
5: 0.06860159475429536
6: 0.09864639036375641
7: 0.1397219083798082
8: 0.06893217366056492
9: 0.10644608412010759
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.10533172203029124
1: 0.08114541638167035
2: 0.09728823266184927
3: 0.09847571748679061
4: 0.09910306217485612
5: 0.09912314285432645
6: 0.10110447208166495
7: 0.10858911006740113
8: 0.09973419199672241
9: 0.11010493226442747
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10547069738692876
1: 0.1646043649137132
2: 0.09790842215396131
3: 0.08884821851528674
4: 0.0860178648224438
5: 0.08814422821860789
6: 0.10637039314288442
7: 0.0870450558104711
8: 0.0895878644937113
9: 0.08600289054199149
Prediction: 9, Ans: 9

Postirior (in log scale):
0: 0.0938179615630441
1: 0.16463661564539725
2: 0.08937055346603738
3: 0.0909139941225741
4: 0.08777941663749678
5: 0.09028352198496013
6: 0.09

3: 0.09950512102514686
4: 0.09288396133723337
5: 0.08798294782241084
6: 0.09880913632631193
7: 0.06726501407613805
8: 0.09060969389923444
9: 0.1055111321067299
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.09015777368478808
1: 0.18521295076989214
2: 0.08174944373174162
3: 0.07780216525814765
4: 0.0811699179032613
5: 0.081900397674468
6: 0.1225318198710661
7: 0.09153075382359711
8: 0.08244641222699692
9: 0.10549836505604114
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.10903659860578671
1: 0.07980436375113653
2: 0.09735489629666803
3: 0.0985676713169139
4: 0.0989697446944936
5: 0.09909147839877679
6: 0.10023424839796174
7: 0.11298390291039782
8: 0.09998113046051763
9: 0.10397596516734717
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10474727039105018
1: 0.15642211281656457
2: 0.09965003998014074
3: 0.0962872486051115
4: 0.09211277369518002
5: 0.09348993139478189
6: 0.0982783719387411
7: 0.08070593043565805
8: 0.09617326939126246
9: 0.08213305135150949
Prediction:

...

4: 0.0895151288351339
5: 0.08627161282458133
6: 0.09673217144357635
7: 0.1477156685582717
8: 0.08465246417919456
9: 0.13476511316146186
Prediction: 2, Ans: 2

Postirior (in log scale):
0: 0.07554272486292539
1: 0.17372487197031258
2: 0.07170257030009196
3: 0.07033672294560955
4: 0.0915739255134308
5: 0.07354852395175127
6: 0.08814444546437915
7: 0.15495093444876604
8: 0.07562729500833464
9: 0.12484798553439864
Prediction: 3, Ans: 3

Postirior (in log scale):
0: 0.09908343192057502
1: 0.16420569136581792
2: 0.08993807145708563
3: 0.08960627249532176
4: 0.08517770452194842
5: 0.08882566468645917
6: 0.1006013800590552
7: 0.1006687006305357
8: 0.08975067385686926
9: 0.09214240900633199
Prediction: 4, Ans: 4

Postirior (in log scale):
0: 0.10498784354546083
1: 0.11021612566421779
2: 0.10509016090572376
3: 0.10157950551850224
4: 0.0998134207444605
5: 0.0985851010653451
6: 0.11180024360717852
7: 0.08000544189831967
8: 0.10424072874653538
9: 0.08368142830425626
Prediction: 7, Ans: 7

Postirior

Postirior (in log scale):
0: 0.10428919101038932
1: 0.10646841873576936
2: 0.10202881696173742
3: 0.1005391097762056
4: 0.09928291553004982
5: 0.09930160875178452
6: 0.11088433100476044
7: 0.08637995447424884
8: 0.10236628610265495
9: 0.0884593676523998
Prediction: 7, Ans: 9

Postirior (in log scale):
0: 0.10311829533237789
1: 0.07929058754889529
2: 0.09310555764564978
3: 0.09388594135543028
4: 0.09464452005999836
5: 0.09436351402108328
6: 0.0977580637429505
7: 0.12582222819097283
8: 0.09472409469853575
9: 0.12328719740410614
Prediction: 1, Ans: 8

Postirior (in log scale):
0: 0.09895624940249088
1: 0.11982332872111816
2: 0.09242958385748304
3: 0.09237340493402957
4: 0.09369634370630206
5: 0.09360617701207083
6: 0.09575698627428329
7: 0.11029389271491255
8: 0.09428707350479636
9: 0.10877695987251342
Prediction: 3, Ans: 6

Postirior (in log scale):
0: 0.09859339106744734
1: 0.15240352434111878
2: 0.09801035531405111
3: 0.09470712190037728
4: 0.09061191748050179
5: 0.08993349916550954
6:

9: 0.10039181560978834
Prediction: 8, Ans: 2

Postirior (in log scale):
0: 0.10514783410498055
1: 0.09917051194308238
2: 0.10566780477984174
3: 0.10242868077775887
4: 0.10158042177520557
5: 0.10164389646754887
6: 0.10164083560969463
7: 0.08697444929907473
8: 0.10465091872515969
9: 0.09109464651765288
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.10470097438567708
1: 0.1262358049151015
2: 0.1013747371224297
3: 0.0994494867718348
4: 0.09496275617750632
5: 0.09611642735762246
6: 0.10624797399774348
7: 0.08304545039670844
8: 0.10088163038696565
9: 0.08698475848841049
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.11075605843479612
1: 0.08040363846568492
2: 0.09807577083830687
3: 0.098614716376452
4: 0.09823278418592427
5: 0.09925076699265405
6: 0.10756110150264812
7: 0.10653414160366222
8: 0.09946741619896368
9: 0.1011036054009079
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.061254700420106216
1: 0.24543395111257604
2: 0.06320898667151922
3: 0.06788490791039298
4: 0

9: 0.07296967358845877
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.08004302158020198
1: 0.18189838354624238
2: 0.08246226646553922
3: 0.08207589741030238
4: 0.08706512381778436
5: 0.08288142173933634
6: 0.09161291082981589
7: 0.11480589932943716
8: 0.08354380899176016
9: 0.11361126628958017
Prediction: 0, Ans: 0

Postirior (in log scale):
0: 0.11056421290026942
1: 0.08033483166867252
2: 0.09919887923477982
3: 0.09877480245986643
4: 0.09904920600008156
5: 0.09942926883478381
6: 0.1112128794808947
7: 0.10129083200259774
8: 0.09999779456610446
9: 0.10014729285194934
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.10100376759264523
1: 0.21212583887818331
2: 0.09833679927084503
3: 0.0842867188040272
4: 0.07800408753700669
5: 0.08225913258839962
6: 0.10273403490969388
7: 0.07990809907359483
8: 0.0826890206415328
9: 0.07865250070407134
Prediction: 4, Ans: 9

Postirior (in log scale):
0: 0.07603025977751486
1: 0.2190113582860586
2: 0.056755019521107265
3: 0.060316087733837724
4

5: 0.08797550478590813
6: 0.13020875273745738
7: 0.11391587113012049
8: 0.0878500920604426
9: 0.10308825322194254
Prediction: 8, Ans: 8

Postirior (in log scale):
0: 0.10581840111766815
1: 0.13514748991830497
2: 0.10516193558103877
3: 0.09720046423089053
4: 0.1025655594147023
5: 0.09492142262452616
6: 0.09761316983901237
7: 0.07905975116721987
8: 0.09880643971082548
9: 0.0837053663958113
Prediction: 7, Ans: 7

Postirior (in log scale):
0: 0.10944763338835907
1: 0.07980154039532154
2: 0.09707164812027268
3: 0.09785797796051662
4: 0.09766734332974558
5: 0.09828004569321144
6: 0.10797925377344907
7: 0.1109877234775138
8: 0.09835298536974699
9: 0.10255384849186337
Prediction: 1, Ans: 1

Postirior (in log scale):
0: 0.08394730528450962
1: 0.13680478165690158
2: 0.07790041172958452
3: 0.08085811366403785
4: 0.09388689890232288
5: 0.08091934122509058
6: 0.08196029249673246
7: 0.13032037404204266
8: 0.09299229451346265
9: 0.1404101864853151
Prediction: 2, Ans: 5

Postirior (in log scale):
0: 0

In [7]:
print("Imagination of numbers in Bayesian classifier: ")
for label in range(10):
    temp = []
    for pixels in condiction_probability3D[label]:
        max_pixel_range_index = np.argmax(pixels)  # 選出淡到黑機率最大的pixel_range index
        if max_pixel_range_index >= 128:            # 因為>=128是1(黑) 
            temp.append(1)
        else:
            temp.append(0)
    
    # 印出數字 #
    print("{}:".format(label))
    for i in range(len(temp)):
        if i != 0 and i % 28 == 0:
            print()
        print(temp[i], end="")
    print()

Imagination of numbers in Bayesian classifier: 
0:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000001110000000000
0000000000000111111100000000
0000000000001111111110000000
0000000000011111111110000000
0000000000111110001111000000
0000000001111000000111000000
0000000001110000000011100000
0000000011100000000011100000
0000000111100000000011100000
0000000111000000000011100000
0000000111000000000011000000
0000001110000000000111000000
0000001110000000000110000000
0000001110000000001110000000
0000001111000000111100000000
0000000111110011111000000000
0000000111111111110000000000
0000000011111111000000000000
0000000000111100000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
1:
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
0000000000000000000000000000
000000000000000000